In [2]:
import os 
import glob
from skimage import io 
import numpy as np
import matplotlib.pyplot as plt
import re 
%matplotlib inline

In [1]:
# Set output directory for new images; /hpc/scratch/hdd2/fs541623/pre-processed_Images
parent_dir = '/hpc/scratch/hdd2/fs541623/'
data_dir = os.path.join(parent_dir, 'QST')
output_dir = os.path.join(parent_dir, 'Pre_processed_Images')
img_file_list = sorted(glob.glob(os.path.join(data_dir, '*RPTEC*/*/Image/*.tif')), key=os.path.getctime)

NameError: name 'os' is not defined

In [3]:
img_file_list = sorted(glob.glob('/hpc/scratch/hdd2/fs541623/Pre_processed_Images/*/*'))
for i in img_file_list:
    print(i)

/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R1/Well_08
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R1/Well_09
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R1/Well_10
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R1/Well_11
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R1/Well_14
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R1/Well_15
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R1/Well_16
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R1/Well_17
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R2/Well_08
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R2/Well_09
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R2/Well_10
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R2/Well_11
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R2/Well_14
/hpc/scratch/hdd2/fs541623/Pre_processed_Images/Time_16hrs_R2/Well_15
/hpc/scratch/hdd2/fs

In [ ]:
# Take max of C4 & C5 as both Red and C4 is marker which goes inside cells and C5 is annexin marker bind outside cells (check)

# Do MaxZ of PI, Annexin  
for i, n in enumerate(img_file_list):
    
    # Get Timepoint 
    timepoint_re = re.compile(r'\d+hrs_R\d')
    timepoint = 'Time_' + str(timepoint_re.findall(os.path.dirname(n))[0])

    # Get Well Number 
    Well_re = re.compile(r'W\d{2}(\d+)')
    Well_no = 'Well_' + str(Well_re.findall(str(n))[0])
        
    # Get Field Number 
    Field_re = re.compile(r'F\d{3}(\d)')
    Field_no = 'Field_' + str(Field_re.findall(str(n))[0])
    
    # Get Channel Number 
    Channel_re = re.compile(r'C(\d)')
    channel_no = 'C' + str(Channel_re.findall(str(n))[0])
    print(f'channel number : {channel_no}')
    
    # Paths to Brightfield and Single Channel Images 
    path_C1 = os.path.join(output_dir, timepoint, Well_no, 'Brightfield') 
    path_B = os.path.join(output_dir, timepoint, Well_no, 'Nuc')
    path_G = os.path.join(output_dir, timepoint, Well_no, 'Cyt')
    path_pi = os.path.join(output_dir, timepoint, Well_no, 'PI') 
    path_AnnexinV = os.path.join(output_dir, timepoint, Well_no, 'AnnexinV') 
    
    
    # Save Brightfield Channel - middle Z 
    if 'Z003C1' in str(n):
        img_C1 = io.imread(n) 
        print(n)
        
        # Create New directory for each Timepoint and Well
        if not os.path.exists(path_C1):
            os.makedirs(path_C1)
        Brightfield_name = f'{timepoint}_{Well_no}_{Field_no}_{channel_no}.tif'
        io.imsave(os.path.join(path_C1, Brightfield_name), img_C1)
        print('--------------------------------C1 saved-----------------------------------------')

    
    # Save Nuclei Image Z003
    elif 'Z003C2' in str(n):
        img_C2 = io.imread(n)
        
        if not os.path.exists(path_B):
            os.makedirs(path_B)
        Nuc_name = f'{timepoint}_{Well_no}_{Field_no}_{channel_no}.tif'
        io.imsave(os.path.join(path_B, Nuc_name), img_C2)
        print('--------------------------------C2 saved-----------------------------------------')

        
    
    # CellMask Image 
    elif 'Z003C3' in str(n):
        
        # Current Cell Mask Image 
        img_C3 = io.imread(n)
        
        if not os.path.exists(path_G):
            os.makedirs(path_G)
        Cyt_name = f'{timepoint}_{Well_no}_{Field_no}_{channel_no}.tif'
        io.imsave(os.path.join(path_G, Cyt_name), img_C3)
        print('--------------------------------C3 saved-----------------------------------------')
        
    
    # PI MaxZ
    elif 'C4' in str(n):
        img_C4 = io.imread(n)
        
        if i < 5:
            prev_Max_C4 = img_C4 

        
        # Update Max of C4
        prev_Max_C4[np.where(prev_Max_C4 < img_C4)] = img_C4[np.where(img_C4 > prev_Max_C4)]
        
        # Save Image 
        if 'Z006C4' in str(n):
            max_c4 = prev_Max_C4
            
            # Create New directory for each Timepoint and Well 
            if not os.path.exists(path_pi):
                os.makedirs(path_pi)
            pi_name = f'{timepoint}_{Well_no}_{Field_no}_{channel_no}.tif'
            io.imsave(os.path.join(path_pi, pi_name), max_c4)

            print('-----------------------------Max PI Saved-----------------------------------------')


        
    # AnnexinV MaxZ
    elif 'C5' in str(n):
        img_C5 = io.imread(n)
        
        if i < 5:
            prev_Max_C5 = img_C5 
        
        # Update Max of C5
        prev_Max_C5[np.where(prev_Max_C5 < img_C5)] = img_C5[np.where(img_C5 > prev_Max_C5)]
        
        if 'Z006C5' in str(n):
            max_C5 = prev_Max_C5
            
            # Create New directory for each Timepoint and Well 
            if not os.path.exists(path_AnnexinV):
                os.makedirs(path_AnnexinV)
            annexinV_name = f'{timepoint}_{Well_no}_{Field_no}_{channel_no}.tif'
            io.imsave(os.path.join(path_AnnexinV, annexinV_name), max_C5)
            print('---------------------------------------Max Annexin saved-------------------------------------------')
    

OME series: not an ome-tiff master file


channel number : C1
channel number : C2
channel number : C3
channel number : C4


OME series: not an ome-tiff master file


channel number : C5
channel number : C1
channel number : C2
channel number : C3
channel number : C4


OME series: not an ome-tiff master file
OME series: not an ome-tiff master file


...

--------------------------------C2 saved-----------------------------------------
channel number : C3


OME series: not an ome-tiff master file


--------------------------------C3 saved-----------------------------------------
channel number : C4
channel number : C1
channel number : C2
channel number : C3
channel number : C4


OME series: not an ome-tiff master file
OME series: not an ome-tiff master file


channel number : C1
channel number : C2
channel number : C3
channel number : C4
